# Model Selection 

The objective of this notebook is to build a very first ent to end Machine Learning model to predict the probability of a patient being discharged on a particular day.

We'll use the dataset generated by the `dataset` job of the ETL folder. 

At this instance, the focus won't be on model performance but rather on understanding the value potential of the available data and the speedness of the solution.

In [1]:
%cd /Users/josefinadallavia/Documents/MIM/Tesis/AML-hospital

/Users/josefinadallavia/Documents/MIM/Tesis/AML-hospital


In [2]:
import warnings
warnings.filterwarnings('ignore')
import os
import pandas as pd
from matplotlib import pyplot as plt   
os.environ['KMP_DUPLICATE_LIB_OK']='True'
from thesis_lib.utils import * 
from thesis_lib.modelling.data import *
from thesis_lib.modelling.model import *


/Users/josefinadallavia/opt/anaconda3/lib/python3.7/importlib/_bootstrap.py:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 192 from C header, got 216 from PyObject
  return f(*args, **kwds)
/Users/josefinadallavia/opt/anaconda3/lib/python3.7/importlib/_bootstrap.py:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 192 from C header, got 216 from PyObject
  return f(*args, **kwds)
/Users/josefinadallavia/opt/anaconda3/lib/python3.7/importlib/_bootstrap.py:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 192 from C header, got 216 from PyObject
  return f(*args, **kwds)


In [3]:
data = Data().load('data/hospital_dataset')
variables = data.get_variables_dict()
data.get_stats()

Loading dataset:  hospital_train_data.parquet
Loading dataset:  hospital_val_data.parquet
Loading dataset:  hospital_test_data.parquet


dataset_type         train         val        test
n_observations      319150       33482       33309
relative_size      0.82694   0.0867542   0.0863059
n_cols                  71          71          71
positives            42697        4555        4507
negatives           276453       28927       28802
positive_prop     0.133783    0.136043    0.135309
negative_prop     0.866217    0.863957    0.864691
min_date        2017-01-01  2018-11-11  2018-11-11
max_date        2018-11-10  2019-11-11  2019-11-11

In [4]:
sequence_features = ['labos_studies_names','sectors_names','images_study_types','surgeries_types',
                    'surgeries_injury_condition','surgeries_post_surgery_condition','surgeries_anesthesia_types']

In [5]:
text_features = ['administrative_diagnosis','presumptive_dianogsis','images_studies_names',
                'surgeries_actual']

In [6]:
text_features = [ 'administrative_diagnosis','presumptive_dianogsis','images_studies_names',
                'surgeries_actual' ,            
    'labos_studies_names','sectors_names','images_study_types','surgeries_types',
                    'surgeries_injury_condition','surgeries_post_surgery_condition','surgeries_anesthesia_types']

In [7]:
categorical_features = ['date_weekday',
 'request_origin',
 'origin',
 'entity_group',
 'gender',
 'request_sector',
 'insurance_entity',
 'admission_sector',
 'emergency_service',
 'isolation',
 'ARM_TEP',
 'CEC_TEP',
 'request_sector',
 'date_weekday',
 'admission_weekday',
 'date_month',
 'admission_month']

In [8]:
numerical_features = ['PIM2TEP',
 'emergency_service',
 'high_risk_TEP',
 'hosp_day_number',
 'images_count',
 'images_cumulative',
 'images_emergencies',
 'images_requester_roles_count',
 'images_requesters_count',
 'images_study_types_count',
 'labos_count',
 'labos_cumulative',
 'labos_emergencies',
 'labos_requester_roles_count',
 'labos_requesters_count',
 'labos_set_count',
 'labos_set_cumulative',
 'low_risk_TEP',
 'new_born_gestation_age',
 'new_born_weight',
 'patient_age',
 'sectors_count',
 'surgeries_count',
 'surgeries_cumulative',
 'surgeries_post_surgery_duration',
 'surgeries_pre_surgery_duration',
 'surgeries_prep_duration',
 'surgeries_services_count',
 'surgeries_surgery_delay',
 'surgeries_surgery_duration',
 'surgeries_types_count']

### All features

In [9]:
model_params = {'classifier': 'random_forest',
               'accepts_sparse': True,
                'categorical_features' : categorical_features ,
                'numerical_features' : numerical_features,
               'text_features': text_features,
                #'sequence_features':sequence_features
               }

In [10]:
rf_comb_features = Model(**model_params)
rf_comb_features.transform(data)

Fitting pipeline...
	 Preprocessing data
	 Preprocessing data
	 Encoding Categorical Features with OneHotEncoding
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
Transforming data...
	 Transforming numerical features
	 Preprocessing data
	 Transforming categorical features
	 Preprocessing data
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transformi

In [11]:
rf_comb_features.n_features

20089

### Fine tuning

### Objective function

In [12]:
import lightgbm as lgb
import flatdict
from hyperopt import STATUS_OK

N_FOLDS = 3

# Create the dataset
train_set = lgb.Dataset(rf_comb_features.X_train,label=rf_comb_features.y_train)

def objective(params, n_folds = N_FOLDS):
    """Objective function for Gradient Boosting Machine Hyperparameter Tuning"""
    flatten_params = flatdict.FlatDict(params)
    parameters ={param_name: flatten_params[param_name] for param_name in flatten_params}
    
    
    # Perform n_fold cross validation with hyperparameters
    # Use early stopping and evalute based on ROC AUC
    cv_results = lgb.cv(params = parameters, train_set = train_set,
                        nfold = n_folds,
                        num_boost_round=parameters.get('num_boost_round',100),
                        early_stopping_rounds = 100, metrics = 'auc', seed = 2020,
                        verbose_eval=True)
  
    # Extract the best score
    best_score = max(cv_results['auc-mean'])
    
    # Loss must be minimized
    loss = 1 - best_score
    
    # Dictionary with information for evaluation
    return {'loss': loss, 'params': params, 'status': STATUS_OK}

### Domain space

In [13]:
from hyperopt import hp

space_rf = {
    'objective': hp.choice('objective', ['binary']),
  
    'boosting_type': 'rf', 
    
    'bagging_freq': hp.quniform('bagging_freq', 1,20,1), 
    
    'bagging_fraction': hp.uniform('bagging_fraction', 0.5, 0.99),
    
    'max_depth': hp.quniform('max_depth', 5, 30,1),
    
    'learning_rate': hp.loguniform('learning_rate', np.log(0.001), np.log(0.1)),
    
    'num_boost_round': hp.choice('num_iterations', [100,150,200,300,500])
}

In [14]:
import hyperopt.pyll.stochastic 

### Optimization algorithm

In [15]:
from hyperopt import tpe
# Algorithm
tpe_algorithm = tpe.suggest

### Result history

In [16]:
from hyperopt import Trials
# Trials object to track progress
bayes_trials_rf = Trials()

In [17]:
!pwd

/Users/josefinadallavia/Documents/MIM/Tesis/AML-hospital


### Optimization

In [18]:
from hyperopt import fmin

MAX_EVALS = 200

# Optimize
best = fmin(fn = objective, space = space_rf, algo = tpe.suggest, 
            max_evals = MAX_EVALS, trials = bayes_trials_rf)

  0%|          | 0/200 [00:00<?, ?trial/s, best loss=?]

/Users/josefinadallavia/opt/anaconda3/lib/python3.7/site-packages/lightgbm/engine.py:503: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))



[1]	cv_agg's auc: 0.782227 + 0.0023378                 
[2]	cv_agg's auc: 0.782227 + 0.0023378                 
[3]	cv_agg's auc: 0.782227 + 0.0023378                 
[4]	cv_agg's auc: 0.782227 + 0.0023378                 
[5]	cv_agg's auc: 0.792411 + 0.000509532               
[6]	cv_agg's auc: 0.792601 + 0.000423805               
[7]	cv_agg's auc: 0.792606 + 0.000439967               
[8]	cv_agg's auc: 0.792675 + 0.000378186               
[9]	cv_agg's auc: 0.793601 + 0.00033383                
[10]	cv_agg's auc: 0.793745 + 0.000405298              
[11]	cv_agg's auc: 0.793836 + 0.000431693              
[12]	cv_agg's auc: 0.794072 + 0.00051912               
[13]	cv_agg's auc: 0.795567 + 0.000652906              
[14]	cv_agg's auc: 0.795698 + 0.000740993              
[15]	cv_agg's auc: 0.795826 + 0.000693208              
[16]	cv_agg's auc: 0.795752 + 0.0007114                
[17]	cv_agg's auc: 0.796051 + 0.000549702              
[18]	cv_agg's auc: 0.795653 + 0.000473633       

[147]	cv_agg's auc: 0.797996 + 0.00037491              
[148]	cv_agg's auc: 0.797989 + 0.000372846             
[149]	cv_agg's auc: 0.797972 + 0.000341364             
[150]	cv_agg's auc: 0.797931 + 0.000279351             
[151]	cv_agg's auc: 0.797904 + 0.000287253             
[152]	cv_agg's auc: 0.797898 + 0.000276622             
[153]	cv_agg's auc: 0.797943 + 0.000249996             
[154]	cv_agg's auc: 0.797971 + 0.000243972             
[155]	cv_agg's auc: 0.797937 + 0.000186264             
[156]	cv_agg's auc: 0.797929 + 0.000174267             
[157]	cv_agg's auc: 0.79794 + 0.000193144              
[158]	cv_agg's auc: 0.797932 + 0.000184842             
[159]	cv_agg's auc: 0.79793 + 0.000190828              
[160]	cv_agg's auc: 0.797934 + 0.000209776             
[161]	cv_agg's auc: 0.798058 + 0.000192653             
[162]	cv_agg's auc: 0.798092 + 0.000228158             
[163]	cv_agg's auc: 0.798099 + 0.000223136             
[164]	cv_agg's auc: 0.798086 + 0.00025351       

[293]	cv_agg's auc: 0.799172 + 0.000136544             
[294]	cv_agg's auc: 0.799173 + 0.000139115             
[295]	cv_agg's auc: 0.799178 + 0.000131064             
[296]	cv_agg's auc: 0.799163 + 0.000124454             
[297]	cv_agg's auc: 0.799182 + 0.000134348             
[298]	cv_agg's auc: 0.799189 + 0.000136318             
[299]	cv_agg's auc: 0.799191 + 0.000140659             
[300]	cv_agg's auc: 0.799213 + 0.000158984             
[301]	cv_agg's auc: 0.799233 + 0.000144491             
[302]	cv_agg's auc: 0.799239 + 0.000134724             
[303]	cv_agg's auc: 0.799247 + 0.000119798             
[304]	cv_agg's auc: 0.799263 + 0.000104555             
[305]	cv_agg's auc: 0.799264 + 9.63003e-05             
[306]	cv_agg's auc: 0.799266 + 9.63802e-05             
[307]	cv_agg's auc: 0.799276 + 8.02064e-05             
[308]	cv_agg's auc: 0.799274 + 8.05614e-05             
[309]	cv_agg's auc: 0.799269 + 8.43272e-05             
[310]	cv_agg's auc: 0.7993 + 8.04744e-05        

...

/Users/josefinadallavia/opt/anaconda3/lib/python3.7/site-packages/lightgbm/engine.py:503: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))



[1]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[2]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[3]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[4]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[5]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[6]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[7]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[8]	cv_agg's auc: 0.782672 + 0.00118665                                                 
[9]	cv_agg's auc: 0.792665 + 0.00161745                                                 
[10]	cv_agg's auc: 0.793429 + 0.00206483                                                
[11]	cv_agg's auc: 0.793825 + 0.00167163                                                
[12]	cv_agg's auc: 0.

[93]	cv_agg's auc: 0.79969 + 0.0010559                                                  
[94]	cv_agg's auc: 0.799703 + 0.00106558                                                
[95]	cv_agg's auc: 0.799705 + 0.00106286                                                
[96]	cv_agg's auc: 0.79972 + 0.00111509                                                 
[97]	cv_agg's auc: 0.799746 + 0.00109979                                                
[98]	cv_agg's auc: 0.799793 + 0.00110364                                                
[99]	cv_agg's auc: 0.799794 + 0.00111043                                                
[100]	cv_agg's auc: 0.799783 + 0.00108669                                               
[101]	cv_agg's auc: 0.799779 + 0.00107545                                               
[102]	cv_agg's auc: 0.799757 + 0.00109115                                               
[103]	cv_agg's auc: 0.799745 + 0.00108632                                               
[104]	cv_agg's auc: 0

[185]	cv_agg's auc: 0.800214 + 0.000808026                                              
[186]	cv_agg's auc: 0.80019 + 0.000812598                                               
[187]	cv_agg's auc: 0.800184 + 0.000816894                                              
[188]	cv_agg's auc: 0.800191 + 0.000822992                                              
[189]	cv_agg's auc: 0.800182 + 0.000819055                                              
[190]	cv_agg's auc: 0.800173 + 0.000816822                                              
[191]	cv_agg's auc: 0.800166 + 0.000822408                                              
[192]	cv_agg's auc: 0.800164 + 0.000832161                                              
[193]	cv_agg's auc: 0.800182 + 0.000821263                                              
[194]	cv_agg's auc: 0.800174 + 0.000824672                                              
[195]	cv_agg's auc: 0.800161 + 0.000836143                                              
[196]	cv_agg's auc: 0

[277]	cv_agg's auc: 0.800539 + 0.000771162                                              
[278]	cv_agg's auc: 0.800533 + 0.000786893                                              
[279]	cv_agg's auc: 0.800536 + 0.000799176                                              
[280]	cv_agg's auc: 0.800513 + 0.000816344                                              
[281]	cv_agg's auc: 0.800507 + 0.000800229                                              
[282]	cv_agg's auc: 0.800498 + 0.000797975                                              
[283]	cv_agg's auc: 0.800494 + 0.000784069                                              
[284]	cv_agg's auc: 0.800511 + 0.000774792                                              
[285]	cv_agg's auc: 0.800531 + 0.000792673                                              
[286]	cv_agg's auc: 0.800527 + 0.000784317                                              
[287]	cv_agg's auc: 0.800537 + 0.000791934                                              
[288]	cv_agg's auc: 0

In [19]:
bayes_trials_rf.results

[{'loss': 0.2006530130565909,
  'params': {'bagging_fraction': 0.7266409683041658,
   'bagging_freq': 4,
   'boosting_type': 'rf',
   'learning_rate': 0.010813929380508553,
   'max_depth': 27,
   'num_boost_round': 500,
   'objective': 'binary'},
  'status': 'ok'},
 {'loss': 0.19955517123631739,
  'params': {'bagging_fraction': 0.5731927993790715,
   'bagging_freq': 11,
   'boosting_type': 'rf',
   'learning_rate': 0.03443560256040207,
   'max_depth': 7,
   'num_boost_round': 150,
   'objective': 'binary'},
  'status': 'ok'},
 {'loss': 0.20077648177914098,
  'params': {'bagging_fraction': 0.6794248751911931,
   'bagging_freq': 18,
   'boosting_type': 'rf',
   'learning_rate': 0.006114900879216385,
   'max_depth': 14,
   'num_boost_round': 200,
   'objective': 'binary'},
  'status': 'ok'},
 {'loss': 0.20123510006690593,
  'params': {'bagging_fraction': 0.6440173312454063,
   'bagging_freq': 19,
   'boosting_type': 'rf',
   'learning_rate': 0.03447753487131953,
   'max_depth': 15,
   'nu

In [20]:
rf_results = []
for result in bayes_trials_rf.results:
    flatten_results = flatdict.FlatDict(result)
    dict_results = {key: flatten_results[key] for key in flatten_results}
    rf_results.append(dict_results)

In [21]:
filename = '/Users/josefinadallavia/Documents/MIM/Tesis/AML-hospital/experiments/rf_auto_ml_results.csv'

In [22]:
import csv
fieldnames = list(rf_results[0].keys())
    
with open(filename, 'w') as output_file:
    writer = csv.DictWriter(output_file, fieldnames=fieldnames)
    writer.writeheader()
    writer.writerows(rf_results)

In [24]:
best

{'bagging_fraction': 0.5007548070451577,
 'bagging_freq': 2.0,
 'learning_rate': 0.015108753451492058,
 'max_depth': 6.0,
 'num_iterations': 3,
 'objective': 0}